In [1]:
import os
fastas  = os.listdir("00_CAFPdb_fastas")
fastas  = [x for x in fastas if x[-3:]==".fa"]
DBnames = [x.split("_")[1] for x in fastas]
fastas, DBnames

(['Antifungal_APD3_2022_1230.fa',
  'Antifungal_CAMPR3_2022_1144.fa',
  'Antifungal_DBAASP3_2022_5579.fa',
  'Antifungal_DRAMP3_2022_1802.fa',
  'Antifungal_PAMP_2022_80.fa',
  'Antifungal_PPDB_2022_529.fa',
  'Antifungal_LPDB_2022_42.fa',
  'Antifungal_EROP_2022_802.fa',
  'Antifungal_SATPDB_2022_1435.fa',
  'Antifungal_ALLDB.fa'],
 ['APD3',
  'CAMPR3',
  'DBAASP3',
  'DRAMP3',
  'PAMP',
  'PPDB',
  'LPDB',
  'EROP',
  'SATPDB',
  'ALLDB.fa'])

In [2]:
def do_clustering(database, fasta, minseqid, outdir="03_MMseqs2_Clustering"):
    #Clustering with mmseqs2
    cmd0 = "mmseqs createdb 00_CAFPdb_fastas/{2} {1}/{0}".format(database, outdir, fasta)
    cmd1 = "mmseqs cluster --min-seq-id {2} --cluster-mode 0 {1}/{0} {1}/{0}_clu{2} {1}/tmp".format(database,outdir,minseqid)
    #Output human readable
    cmd2 = "mmseqs createtsv {1}/{0} {1}/{0} {1}/{0}_clu{2} {1}/{0}_clu{2}.tsv".format(database,outdir,minseqid)
    cmd3 = "mmseqs createseqfiledb {1}/{0} {1}/{0}_clu{2} {1}/{0}_clu{2}_seq".format(database,outdir,minseqid)
    cmd4 = "mmseqs result2flat {1}/{0} {1}/{0} {1}/{0}_clu{2}_seq {1}/{0}_clu{2}_seq.fasta".format(database,outdir,minseqid)
    cmd5 = "mmseqs result2flat {1}/{0} {1}/{0} {1}/{0}_clu{2} {1}/{0}_clu{2}.fasta".format(database,outdir,minseqid)
    #Clustering 
    cmd6 = "mmseqs createsubdb {1}/{0}_clu{2} {1}/{0} {1}/{0}_clu{2}_rep".format(database,outdir,minseqid)
    cmd7 = "mmseqs convert2fasta {1}/{0}_clu{2}_rep {1}/{0}_clu{2}_rep.fa".format(database,outdir,minseqid)
    cmd8 = "mmseqs result2stats {1}/{0} {1}/{0} {1}/{0}_clu{2} {1}/{0}_clu{2}_sizes --stat linecount".format(database,outdir,minseqid)
    
    # Running commands
    # Si sale 0 esta todo OK
    import os
    try: os.mkdir(outdir)
    except:pass
    
    os.system(cmd0)
    os.system(cmd1)
    os.system(cmd2)
    os.system(cmd3)
    os.system(cmd4)
    os.system(cmd5)
    os.system(cmd6)
    os.system(cmd7)
    os.system(cmd8)
    print ("Finish:", database, minseqid)
    return

def get_dataframe(database,minseqid):
    "Read results and obtain dataframe"
    df = pd.read_csv("03_MMseqs2_Clustering/"+"{0}_clu{1}.tsv".format(database,minseqid), sep='\t', header=None)
    df.columns = ['cluster-representative','cluster-members']
    df2 = df.groupby(['cluster-representative']).count().reset_index()
    df2.sort_values('cluster-members', ascending=False, inplace=True)
    df2['Min_Seq_Ident']=minseqid
    return df2

In [3]:
# Database Selection
selection     = -1 #Perform only the ALL Fastas; for particular DB analysis change these value
scanning_down = 0.2
step          = -0.1
database  = DBnames[selection]
fasta     = fastas[selection]

import pandas as pd
import numpy as np
df = pd.DataFrame()

for minseqid in np.arange(1.0,scanning_down, step):
    minseqid = np.round(minseqid,1)
    print(minseqid)
    import os.path
    if os.path.exists("03_MMseqs2_Clustering/"+"{0}_clu{1}.tsv".format(database,minseqid)):pass
    else: do_clustering(database, fasta, minseqid, outdir="03_MMseqs2_Clustering")
    
    df0 = get_dataframe(database,minseqid)
    df = pd.concat([df, df0],ignore_index=True)
    
df

1.0
0.9
0.8
0.7
0.6
0.5
0.4
0.3


cluster-representative  cluster-members  \
0                                     CAMPSQ3396               24   
1                                    DBASSP3_787               21   
2                                     DRAMP21000               20   
3                                   DBASSP3_5517               20   
4      E05603|Histatin3[1425]|human(Homosapiens)               18   
...                                          ...              ...   
33809                              DBASSP3_18356                1   
33810                              DBASSP3_18357                1   
33811                              DBASSP3_18358                1   
33812                              DBASSP3_18359                1   
33813                                satpdb29091                1   

       Min_Seq_Ident  
0                1.0  
1                1.0  
2                1.0  
3                1.0  
4                1.0  
...              ...  
33809            0.3  
33810            0.3  
33811            0.3  
33812            0.3  
33813            0.3  

[33814 rows x 3 columns]

In [4]:
import altair as alt
alt.data_transformers.disable_max_rows()
bar_chart = alt.Chart(df).mark_bar().encode(
    alt.X('Min_Seq_Ident:O'),
    alt.Y('count(Min_Seq_Ident):Q')
).properties(
    width=600,
    height=600,
    title="Antifungal Peptide Database Size"
)

text = bar_chart.mark_text(
 align='center',
 baseline='middle',
 dy=-5
).encode(
 text="count(Min_Seq_Ident):Q"
)

plot07 = bar_chart + text
plot07.save("03_MMseqs2_Clustering/"+"07plot_ClusteringUnique.html")
plot07.save("03_MMseqs2_Clustering/"+"07plot_ClusteringUnique.svg")
plot07.save("03_MMseqs2_Clustering/"+"07plot_ClusteringUnique.png")
plot07

(not in PATH env variable)


alt.LayerChart(...)

In [5]:
import altair as alt
plot08 = alt.Chart(df).mark_bar().encode(
    alt.X('cluster-members:N'),
    alt.Y('count(cluster-members):Q', scale=alt.Scale(type='log', domain=[0.1, 5000])),
    #column='Min_Seq_Ident:N'
).properties(
    width=1000,
    height=100
).facet(
    facet='Min_Seq_Ident:N',
    columns=1
)

plot08.save("03_MMseqs2_Clustering/"+"08plot_ClusteringDistribution.html")
plot08.save("03_MMseqs2_Clustering/"+"08plot_ClusteringDistribution.svg")
plot08.save("03_MMseqs2_Clustering/"+"08plot_ClusteringDistribution.png")
plot08

alt.FacetChart(...)

# Other test

In [6]:
from Bio import SeqIO
import pandas as pd
seq_df = pd.DataFrame()

input_file = "03_MMseqs2_Clustering/"+"{0}_clu{1}_rep.fa".format(database, minseqid)
print(input_file)
fasta_sequences = SeqIO.parse(open(input_file),'fasta')
for i,fasta in enumerate(fasta_sequences):
    name, sequence = fasta.id, str(fasta.seq)
    seq_df[i]=[name,sequence,len(sequence)]

seq_df = seq_df.transpose()
seq_df

03_MMseqs2_Clustering/ALLDB.fa_clu0.3_rep.fa


0                                                  1   2
0         AP00527                               ILGPVISKIGGVLGGLLKNL  20
1         AP00628                            LLGDFFRKSKEKIGKEFKRIVQR  23
2         AP00749         EADEPLWLYKGDNIERAPTTADHPILPSIIDDVKLDPNRRYA  42
3         AP01006         YITCLFRGARCRVYSGRSCCFGYYCRRDFPGSIFGTCSRRNF  42
4         AP01234  FSKYERQKDKRPYSERKNQYTGPQFLYPPERIPPQKVIKWNEEGLP...  62
...           ...                                                ...  ..
3289  satpdb16712                        MEKKSLAGLCFLFLVLFVAQEIVVTEA  27
3290  satpdb18379                                       FLPIPRPILLGL  12
3291  satpdb23061                                               FSar   4
3292  satpdb25690                                       FLPLIGKILGTI  12
3293  satpdb28040                                       FLPIVTNLLSGL  12

[3294 rows x 3 columns]

In [7]:
df = pd.read_csv("03_MMseqs2_Clustering/"+"{0}_clu{1}.tsv".format(database,minseqid), sep='\t', header=None)
df.columns = ['cluster-representative','cluster-members']
df

cluster-representative cluster-members
0              DBASSP3_11539   DBASSP3_11539
1              DBASSP3_11806   DBASSP3_11806
2              DBASSP3_11951   DBASSP3_11951
3              DBASSP3_12154   DBASSP3_12154
4                 CAMPSQ2604      CAMPSQ2604
...                      ...             ...
12647          DBASSP3_10326   DBASSP3_10326
12648          DBASSP3_10893   DBASSP3_10893
12649          DBASSP3_11225   DBASSP3_11225
12650          DBASSP3_11362   DBASSP3_11362
12651          DBASSP3_11362      DRAMP04096

[12652 rows x 2 columns]

In [8]:
len(df['cluster-representative'].unique())

3294

In [9]:
df2 = df.groupby(['cluster-representative']).count().reset_index()
df2.sort_values('cluster-members', ascending=False, inplace=True)
df2['Min_Seq_Ident']=minseqid
df2

cluster-representative  cluster-members  \
2479                                         DRAMP00427              301   
3158                                        satpdb15876              267   
58                                              AP01817              190   
994                                        DBASSP3_1543              145   
2845  E08749|HeveinlikepeptideEechib/l|Europeanspind...              120   
...                                                 ...              ...   
1412                                      DBASSP3_18356                1   
1413                                      DBASSP3_18357                1   
1414                                      DBASSP3_18358                1   
1415                                      DBASSP3_18359                1   
3293                                        satpdb29091                1   

      Min_Seq_Ident  
2479            0.3  
3158            0.3  
58              0.3  
994             0.3  
2845            0.3  
...             ...  
1412            0.3  
1413            0.3  
1414            0.3  
1415            0.3  
3293            0.3  

[3294 rows x 3 columns]

In [10]:
df3 = df.groupby(['cluster-representative']).agg(lambda x: set(x)).reset_index()

In [11]:
df4 = pd.merge(df3,df2, how='inner', left_on='cluster-representative', right_on='cluster-representative').sort_values('cluster-members_y', ascending=False, ignore_index=True)

In [12]:
df4.groupby(['cluster-members_y','Min_Seq_Ident']).count()

cluster-representative  cluster-members_x
cluster-members_y Min_Seq_Ident                                           
1                 0.3                              1820               1820
2                 0.3                               509                509
3                 0.3                               243                243
4                 0.3                               171                171
5                 0.3                               117                117
...                                                 ...                ...
120               0.3                                 1                  1
145               0.3                                 1                  1
190               0.3                                 1                  1
267               0.3                                 1                  1
301               0.3                                 1                  1

[67 rows x 2 columns]

In [13]:
df4

cluster-representative  \
0                                            DRAMP00427   
1                                           satpdb15876   
2                                               AP01817   
3                                          DBASSP3_1543   
4     E08749|HeveinlikepeptideEechib/l|Europeanspind...   
...                                                 ...   
3289                                      DBASSP3_18356   
3290                                      DBASSP3_18357   
3291                                      DBASSP3_18358   
3292                                      DBASSP3_18359   
3293                                        satpdb29091   

                                      cluster-members_x  cluster-members_y  \
0     {AP00982, AP01686, E07388|DefensinEcAMPD2|annu...                301   
1     {E12051|Brevinin1CG2|Chungantorrentfrog(Amolop...                267   
2     {DRAMP00429, E20821|AntifungalpeptideHcAFP4|bl...                190   
3     {DBASSP3_3719, satpdb24837, AP01876, DRAMP0137...                145   
4     {PPepDB_2386, DBASSP3_5518, E08751|Heveinlikep...                120   
...                                                 ...                ...   
3289                                    {DBASSP3_18356}                  1   
3290                                    {DBASSP3_18357}                  1   
3291                                    {DBASSP3_18358}                  1   
3292                                    {DBASSP3_18359}                  1   
3293                                      {satpdb29091}                  1   

      Min_Seq_Ident  
0               0.3  
1               0.3  
2               0.3  
3               0.3  
4               0.3  
...             ...  
3289            0.3  
3290            0.3  
3291            0.3  
3292            0.3  
3293            0.3  

[3294 rows x 4 columns]

In [14]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')